In [52]:
from tensorflow.keras.models import Sequential # Библиотека НС прямого распространения
from tensorflow.keras.layers import Dense # Библиотека НС Полносвязные слои
from tensorflow .keras import utils #Библиотека для преобразований данных
from google.colab import files #Библиотека для загрузки файлов
import numpy as np #Библиотека для работы с массивами
import pandas as pd
from sklearn.model_selection import train_test_split

In [2]:
files.upload()

Saving accelerometer.csv to accelerometer.csv


{'accelerometer.csv': b'wconfid,pctid,x,y,z\r\n1,20,1.004,0.090,-0.125\r\n1,20,1.004,-0.043,-0.125\r\n1,20,0.969,0.090,-0.121\r\n1,20,0.973,-0.012,-0.137\r\n1,20,1.000,-0.016,-0.121\r\n1,20,0.961,0.082,-0.121\r\n1,20,0.973,-0.055,-0.109\r\n1,20,1.000,0.012,-0.133\r\n1,20,0.969,-0.102,-0.141\r\n1,20,0.973,-0.059,-0.125\r\n1,20,1.012,0.043,-0.133\r\n1,20,0.996,-0.109,-0.148\r\n1,20,0.988,-0.020,-0.125\r\n1,20,1.012,0.043,-0.129\r\n1,20,0.996,-0.090,-0.152\r\n1,20,0.965,-0.102,-0.117\r\n1,20,1.004,0.055,-0.121\r\n1,20,0.988,-0.059,-0.141\r\n1,20,0.969,-0.086,-0.117\r\n1,20,1.039,0.094,-0.117\r\n1,20,0.984,0.113,-0.148\r\n1,20,1.008,0.012,-0.141\r\n1,20,0.996,0.035,-0.141\r\n1,20,0.988,-0.066,-0.125\r\n1,20,0.965,-0.156,-0.113\r\n1,20,0.992,0.059,-0.129\r\n1,20,0.992,-0.031,-0.125\r\n1,20,0.973,-0.133,-0.148\r\n1,20,1.031,0.102,-0.145\r\n1,20,0.984,-0.035,-0.125\r\n1,20,0.984,-0.004,-0.137\r\n1,20,1.000,0.098,-0.125\r\n1,20,1.031,-0.012,-0.129\r\n1,20,0.965,-0.148,-0.152\r\n1,20,1.012,0.10

In [53]:
# считывание жанных из файла
data = pd.read_csv('accelerometer.csv')
X = data.iloc[:,:data.shape[1]-1]
Y = data.iloc[:,data.shape[1]-1]
X_train, X_test, y_train, y_test =  train_test_split(X,Y, test_size=0.33)

# стандартизация данных
mean = X_train.mean(axis=0)
std=X_train.std(axis=0)
X_train -=mean
X_train /=std
X_test -=mean
X_test  /=std
print('Обучающие данные')
pd.concat([X_train.iloc[:300,:],y_train.iloc[:300]], axis=1)

Обучающие данные


wconfid     pctid         x         y      z
37595  -1.225517  0.816404 -1.836388 -1.649689  0.727
50766  -1.225517  1.632021  2.469078 -5.865806  0.543
46129  -1.225517  1.428116 -0.208696 -2.547829  0.203
38818  -1.225517  0.816404  1.652636  1.647999  0.832
113208  1.226474 -1.018733 -0.041254 -0.042776 -0.094
...          ...       ...       ...       ...    ...
12993  -1.225517 -0.814829 -0.036062  0.046497 -0.246
32319  -1.225517  0.408596  0.257286  0.464456  0.570
117880  1.226474 -0.610925  0.065182  0.024855 -0.141
44466  -1.225517  1.224212  0.187194 -5.982132 -1.352
80860   0.000478  0.204692  0.035328  0.210164 -0.398

[300 rows x 5 columns]

In [54]:
print('Тестовые данные')  
pd.concat([X_test.iloc[:300,:],y_test.iloc[:300]], axis=1)

Тестовые данные


wconfid     pctid         x         y      z
73372   0.000478 -0.203116  0.136572 -0.144223  0.055
71846   0.000478 -0.407021 -0.067214  0.068139 -0.199
90024   0.000478  1.020308  0.581786 -0.307890  0.238
45579  -1.225517  1.428116  0.075566 -1.105936 -0.855
142394  1.226474  1.020308 -0.056830  0.083018 -0.137
...          ...       ...       ...       ...    ...
115595  1.226474 -0.814829  0.054798  0.041086 -0.102
150362  1.226474  1.632021  0.166426 -0.148281 -0.227
87888   0.000478  0.816404  0.089844 -0.820533 -0.727
14768  -1.225517 -0.814829 -0.001016 -0.175333 -0.219
81774   0.000478  0.408596 -0.046446  0.659234 -0.090

[300 rows x 5 columns]

In [55]:
def build_model(numberNeurons1,numberNeurons2, optimizer, activation,size):
  model = Sequential()
  # Добавим к модели полносвязный слой с узлами(нейронами):
  model.add(Dense(numberNeurons1,input_shape=(X_train.shape[1],), activation=activation))
  for i in range(size):
    model.add(Dense(numberNeurons2, activation=activation))
  #исп. линейную ф-ию активации для выходного слоя, которая позволяет получать спектр зн-ий, а не только бинарный ответ
  model.add(Dense(1, activation='linear'))
  #производим компиляцию нашей модели
  model.compile(optimizer=optimizer, loss='mse',  metrics=['mae']) 

  return model



In [56]:
import matplotlib.pyplot as plt

def create_plot(history):
  plt.title('Loss / Mean Squared Error')
  plt.plot(history.history['loss'], label='train')
  plt.plot(history.history['val_loss'], label='test')
  plt.legend()
  plt.show()

In [69]:
model = build_model(50,50,"adam",'relu',2)
print(model.summary()) #вывод структуры НС (кол-во слоев, сколько там нейронов, кол-во обучаемых параметров-весовые коеффициенты НС)

Model: "sequential_28"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 dense_112 (Dense)           (None, 50)                250       
                                                                 
 dense_113 (Dense)           (None, 50)                2550      
                                                                 
 dense_114 (Dense)           (None, 50)                2550      
                                                                 
 dense_115 (Dense)           (None, 1)                 51        
                                                                 
Total params: 5,401
Trainable params: 5,401
Non-trainable params: 0
_________________________________________________________________
None


In [76]:
#обучение модели
history = model.fit(X_train, y_train, epochs=25, batch_size=128,   validation_split=0.1,  verbose=1) #визуализация хода обучения

Epoch 1/25
721/721 [==============================] - 3s 4ms/step - loss: 0.2634 - mae: 0.2469 - val_loss: 0.2781 - val_mae: 0.2547
Epoch 2/25
721/721 [==============================] - 3s 4ms/step - loss: 0.2632 - mae: 0.2475 - val_loss: 0.2773 - val_mae: 0.2515
Epoch 3/25
721/721 [==============================] - 3s 4ms/step - loss: 0.2632 - mae: 0.2470 - val_loss: 0.2773 - val_mae: 0.2495
Epoch 4/25
721/721 [==============================] - 3s 4ms/step - loss: 0.2632 - mae: 0.2470 - val_loss: 0.2771 - val_mae: 0.2491
Epoch 5/25
721/721 [==============================] - 3s 4ms/step - loss: 0.2632 - mae: 0.2468 - val_loss: 0.2770 - val_mae: 0.2481
Epoch 6/25
721/721 [==============================] - 3s 4ms/step - loss: 0.2631 - mae: 0.2468 - val_loss: 0.2783 - val_mae: 0.2571
Epoch 7/25
721/721 [==============================] - 3s 4ms/step - loss: 0.2631 - mae: 0.2468 - val_loss: 0.2767 - val_mae: 0.2491
Epoch 8/25
721/721 [==============================] - 3s 4ms/step - loss: 0.

In [77]:
# Оценка качества
train_mse = model.evaluate(X_train, y_train, verbose=0)
test_mse = model.evaluate(X_test, y_test, verbose=0)
print('Train: ',  train_mse, 'Test: ',test_mse)

Train:  [0.262963205575943, 0.24541041254997253] Test:  [0.26239636540412903, 0.2452879548072815]


In [78]:
pred = model.predict(X_test).flatten() 
for i in range(500):
   print("вычисленное значение НС: ", round(pred[i],3), ", верный результат: ", 
         round(y_test.iloc[i],3), ", разница: ", round(y_test.iloc[i] - pred[i],3))

1578/1578 [==============================] - 2s 1ms/step
вычисленное значение НС:  -0.163 , верный результат:  0.055 , разница:  0.218
вычисленное значение НС:  -0.145 , верный результат:  -0.199 , разница:  -0.054
вычисленное значение НС:  -0.19 , верный результат:  0.238 , разница:  0.428
вычисленное значение НС:  -0.18 , верный результат:  -0.855 , разница:  -0.675
вычисленное значение НС:  -0.139 , верный результат:  -0.137 , разница:  0.002
вычисленное значение НС:  -0.144 , верный результат:  -0.145 , разница:  -0.001
вычисленное значение НС:  -0.143 , верный результат:  -0.121 , разница:  0.022
вычисленное значение НС:  -0.159 , верный результат:  -0.68 , разница:  -0.521
вычисленное значение НС:  -0.26 , верный результат:  -1.371 , разница:  -1.111
вычисленное значение НС:  0.219 , верный результат:  0.789 , разница:  0.57
вычисленное значение НС:  -0.275 , верный результат:  -1.148 , разница:  -0.873
вычисленное значение НС:  -0.141 , верный результат:  -0.125 , разница:  0.01

In [ ]:
#сохраняем НС в файл
model.save("NS.h5")
files.download("NS.h5")

In [ ]:
#ипользование уже обученной НС
from keras.models import load_model
files.upload()
model = load_model("NS.h5")

In [74]:
#Подбор гиперпараметров
NumbersNeurons1=[80,400,40]
NumbersNeurons2=[40,200,20]
MasOptimizer=["adam","rmsprop","rmsprop"]
MasActiv=["relu","sigmoid","sigmoid"]
MaskolSL=[3,0,5]

kolepochs=[25,5,25]
kolbatch_size=[300,32,200]

result = pd.DataFrame([], columns=["numberNeurons1","numberNeurons2 - внут. слои", "optimizer","activation","kolSLoev", "kolepochs","kolbatch_size",
                                   "Train loss && MAE", "Test loss && MAE"])
i=0
for i in range(3):
  model = build_model(NumbersNeurons1[i],NumbersNeurons2[i],MasOptimizer[i],MasActiv[i], MaskolSL[i])
  model.fit(X_train, y_train, epochs=kolepochs[i], batch_size=kolbatch_size[i], validation_split=0.1,  verbose=0)
  train_mse1 = model.evaluate(X_train, y_train, verbose=0)
  test_mse1 = model.evaluate(X_test, y_test, verbose=0)
  result.loc[i]=[NumbersNeurons1[i],NumbersNeurons2[i],MasOptimizer[i],MasActiv[i], MaskolSL[i],kolepochs[i],kolbatch_size[i], train_mse1,test_mse1]


print("\n Таблица подбора гиперпараметров \n")
print(result.to_markdown())





 Таблица подбора гиперпараметров 

|    |   numberNeurons1 |   numberNeurons2 - внут. слои | optimizer   | activation   |   kolSLoev |   kolepochs |   kolbatch_size | Train loss && MAE                         | Test loss && MAE                          |
|---:|-----------------:|------------------------------:|:------------|:-------------|-----------:|------------:|----------------:|:------------------------------------------|:------------------------------------------|
|  0 |               80 |                            40 | adam        | relu         |          3 |          25 |             300 | [0.2514974772930145, 0.2326468527317047]  | [0.25579383969306946, 0.2341614067554474] |
|  1 |              400 |                           200 | rmsprop     | sigmoid      |          0 |           5 |              32 | [0.2660735547542572, 0.255165696144104]   | [0.265344500541687, 0.2548246383666992]   |
|  2 |               40 |                            20 | rmsprop     | sigmoid     